# ProtVec: Amino Acid Embedding Representation of Proteins for Function Classification

## Objectives
1. Extract features from amino acid sequences for machine learning
2. Use features to predict protein family and other structural properties

## Abstract
This project attempts to reproduce the results from [Asgari 2015](http://journals.plos.org/plosone/article?id=10.1371/journal.pone.0141287) and to expand it to phage sequences and their protein families. Currently, Asgari's classification of protein families can be reproduced with his using his [trained embedding.](https://github.com/ehsanasgari/Deep-Proteomics). However, his results cannot be reproduced with current attempts to train using the skip-gram negative sampling method detailed in [this tutorial.](http://adventuresinmachinelearning.com/word2vec-keras-tutorial/) Training samples have been attempted with the SwissProt database. 

## Introduction

Predicting protein function with machine learning methods require informative features that is extracted from data. A natural language processing (NLP) technique, known as Word2Vec is used to represent a word by its context with a vector that encodes for the probability a context would occur for a word. These vectors are effective at representing meanings of words since words with similar meanings would have similar contexts. For example, the word cat and kitten would have similar contexts that they are used in since they have very similar meanings. These words would thus have very similar vectors. 




## Methods
1. Preprocessing
  1. Load dataset containing protein amino acid sequences and Asgari's embedding
  2. [Convert sequences to three lists of non-overlapping 3-mer words](https://www.researchgate.net/profile/Mohammad_Mofrad/publication/283644387/figure/fig4/AS:341292040114179@1458381771303/Protein-sequence-splitting-In-order-to-prepare-the-training-data-each-protein-sequence.png) 
  3. Convert 3-mers to numerical encoding using kmer indicies from Asgari's embedding (row dimension)
  4. Generate skipgrams with [Keras function](https://keras.io/preprocessing/sequence/)  
        Output: [target word, context word](http://mccormickml.com/assets/word2vec/training_data.png), label  
        Label refers to true or false target/context pairing generated for the negative sampling technique             
2. Training embedding
    1. Create negative sampling skipgram model with Keras [using technique from this tutorial](http://adventuresinmachinelearning.com/word2vec-keras-tutorial/)
3. Generate ProtVecs from embedding for a given protein sequence
    1. Break protein sequence to list of kmers
    2. Convert kmers to vectors by taking the dot product of its one hot vector with the embedding 
    3. Sum up all vectors for all kmers for a single vector representation for a protein (length 100)        
4. Classify protein function with ProtVec features (results currently not working, refer to R script)
    1. Use protvecs as training features
    2. Use pfam as labels
    3. For a given pfam classification, perform binary classification with all of its positive samples and randomly sample an equal amount of negative samples
    4. Train SVM model 
    
    
## Resources 
1. Intuition behind Word2Vec http://mccormickml.com/2016/04/19/word2vec-tutorial-the-skip-gram-model/
2. Tutorial followed for implementation of skip-gram negative sampling (includes code) http://adventuresinmachinelearning.com/word2vec-keras-tutorial/
3. Introduction to protein function prediction
http://biofunctionprediction.org/cafa-targets/Introduction_to_protein_prediction.pdf



In [1]:
import pandas as pd
import numpy as np
from keras.preprocessing.sequence import skipgrams, pad_sequences, make_sampling_table
from keras.preprocessing.text import hashing_trick
from keras.layers import Embedding, Input, Reshape, Dense, merge
from keras.models import Sequential, Model
from sklearn.manifold import TSNE
from joblib import Parallel, delayed
import multiprocessing

import csv


#Load Ehsan Asgari's embeddings
#Source: http://journals.plos.org/plosone/article?id=10.1371/journal.pone.0141287
#Embedding: https://github.com/ehsanasgari/Deep-Proteomics
ehsanEmbed =  []
with open("protVec_100d_3grams.csv") as tsvfile:
    tsvreader = csv.reader(tsvfile, delimiter="\t")
    for line in tsvreader:
        ehsanEmbed.append(line[0].split('\t'))
threemers = [vec[0] for vec in ehsanEmbed]
embeddingMat = [[float(n) for n in vec[1:]] for vec in ehsanEmbed]
embeddingMat = np.array([embeddingMat])
threemersidx = {} #generate word to index translation dictionary
for i, kmer in enumerate(threemers):
    threemersidx[kmer] = i

#Load NCBI Phage processed dataset - 38420 sequences
table = pd.read_csv("90filter.ncbi.statis_phage_gene.csv", index_col=0)
#Remove entries without vector representation due to amino acid sequence not reaching threshold length
table = table[table['Protein'].apply(lambda x: type(x)!=float)]
table[:10]

#Load Second NCBI Phage processed dataset - 99520 sequences
cherry = pd.read_csv("CherryProteins.csv")
cherry = cherry.loc[cherry['Component'] != 'HYP'] #Filter hypothetical sequences
cherry  = cherry.loc[cherry['Component'] != 'UNS'] #Filter unsorted sequences
cherryseqs = pd.read_csv("cherryaaseqs.csv")

#Load SwissProt 2015 data
swissprot = pd.read_csv("family_classification_metadata.tab", sep='\t')
swissprot['Sequence'] = pd.read_csv("family_classification_sequences.tab", sep='\t')

#Create non-redundant, concatenated sequences list between two NCBI datasets for training
#seqsunique = [seq[0] for seq in cherryseqs['Protein'].values if seq not in table['Protein'].values]
#uniqueinds = [i for i in range(len(cherryseqs)) if cherryseqs['Protein'].iloc[i] not in table['Protein'].values]
#cherryunq = cherryseqs.iloc[uniqueinds]
#cherryunq = cherryunq.append(table[['Function','Protein']])
cherryunq = pd.read_csv("cherryall.csv")

#Set parameters
vocabsize = len(threemersidx)
window_size=25
num_cores = multiprocessing.cpu_count() #For parallel computing

#Path to model weights
weightspath = '38420sample10000000epochsAsgari.hdf'

Using TensorFlow backend.


In [2]:
#Convert sequences to three lists of non overlapping 3mers 
def kmerlists(seq):
    kmer0 = []
    kmer1 = []
    kmer2 = []
    for i in range(0,len(seq)-2,3):
        if len(seq[i:i+3]) == 3:
            kmer0.append(seq[i:i+3])
        i+=1
        if len(seq[i:i+3]) == 3:
            kmer1.append(seq[i:i+3])
        i+=1
        if len(seq[i:i+3]) == 3:
            kmer2.append(seq[i:i+3])
    return [kmer0,kmer1,kmer2]

def kmersindex(seqs, kmersdict):
    kmers = []
    for i in range(len(seqs)):
        kmers.append(kmerlists(seqs[i]))
    kmers = np.array(kmers).flatten().flatten(order='F')
    kmersindex = []
    for seq in kmers:
        temp = []
        for kmer in seq:
            try:
                temp.append(kmersdict[kmer])
            except:
                temp.append(kmersdict['<unk>'])
        kmersindex.append(temp)
    return kmersindex

sampling_table = make_sampling_table(vocabsize)
def generateskipgramshelper(kmersindicies):
    couples, labels = skipgrams(kmersindicies, vocabsize, window_size=window_size, sampling_table=sampling_table)
    if len(couples)==0:
        couples, labels = skipgrams(kmersindicies, vocabsize, window_size=window_size, sampling_table=sampling_table)
    if len(couples)==0:
        couples, labels = skipgrams(kmersindicies, vocabsize, window_size=window_size, sampling_table=sampling_table)
    else:
        word_target, word_context = zip(*couples)
        return word_target, word_context, labels
    
def generateskipgrams(seqs,kmersdict):
    kmersidx = kmersindex(seqs,kmersdict)
    return Parallel(n_jobs=num_cores)(delayed(generateskipgramshelper)(kmers) for kmers in kmersidx)


In [3]:
# create some input variables
input_target = Input((1,))
input_context = Input((1,))
vector_dim = 100

embedding = Embedding(vocabsize, vector_dim, input_length=1, name='embedding')
#embedding.build((None,))
#embedding.set_weights(embeddingMat)
target = embedding(input_target)
target = Reshape((vector_dim, 1))(target)
context = embedding(input_context)
context = Reshape((vector_dim, 1))(context)

# setup a cosine similarity operation which will be output in a secondary model
similarity = merge([target, context], mode='cos', dot_axes=0)

# now perform the dot product operation to get a similarity measure
dot_product = merge([target, context], mode='dot', dot_axes=1)
dot_product = Reshape((1,))(dot_product)
# add the sigmoid output layer
output = Dense(1, activation='sigmoid')(dot_product)

# create the primary training model
model = Model(input=[input_target, input_context], output=output)
model.compile(loss='binary_crossentropy', optimizer='rmsprop')

# create a secondary validation model to run our similarity checks during training
validation_model = Model(input=[input_target, input_context], output=similarity)

#model.load_weights(weightspath)
model.summary()

____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
input_1 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
input_2 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
embedding (Embedding)            (None, 1, 100)        904800      input_1[0][0]                    
                                                                   input_2[0][0]                    
____________________________________________________________________________________________________
reshape_1 (Reshape)              (None, 100, 1)        0           embedding[0][0]         

c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:15: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  from ipykernel import kernelapp as app
c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\keras\legacy\layers.py:458: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:18: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:24: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=[<tf.Tenso..., outputs=Tensor("de...)`
c:\programdat

In [4]:
reverse_dictionary = threemers
vocab_size = vocabsize
class SimilarityCallback:
    def run_sim(self):
        for i in range(valid_size):
            valid_word = reverse_dictionary[valid_examples[i]]
            top_k = 8  # number of nearest neighbors
            sim = self._get_sim(valid_examples[i])
            nearest = (-sim).argsort()[1:top_k + 1]
            log_str = 'Nearest to %s:' % valid_word
            for k in range(top_k):
                close_word = reverse_dictionary[nearest[k]]
                log_str = '%s %s,' % (log_str, close_word)
            print(log_str)

    @staticmethod
    def _get_sim(valid_word_idx):
        sim = np.zeros((vocab_size,))
        in_arr1 = np.zeros((1,))
        in_arr2 = np.zeros((1,))
        for i in range(vocab_size):
            in_arr1[0,] = valid_word_idx
            in_arr2[0,] = i
            out = validation_model.predict_on_batch([in_arr1, in_arr2])
            sim[i] = out
        return sim
sim_cb = SimilarityCallback()

## Training Eshan's embedding with 125,000 phage sequences, random sampling

In [16]:
epochs = 10000000
valid_size = 16
valid_window = 100
valid_examples = np.random.choice(valid_window, valid_size, replace=False)
kmersidx = kmersindex(seqsunique,threemersidx)
thirdlength = int(len(kmersidx)/3)
ite=0

print("Loading part",ite+1,"/ 3 of data, length of ",thirdlength)
kmerskipgrams=generateskipgrams(kmersidx[:thirdlength-1])

arr_1 = np.zeros((1,))
arr_2 = np.zeros((1,))
arr_3 = np.zeros((1,))
for cnt in range(epochs):
    idx = np.random.randint(0, len(kmerskipgrams)-1)
    while type(kmerskipgrams[idx]) != tuple:
        idx = np.random.randint(0, len(kmerskipgrams)-1)
    idx2 = np.random.randint(0,len(kmerskipgrams[idx][0])-1)
    arr_1[0,] = kmerskipgrams[idx][0][idx2]
    arr_2[0,] = kmerskipgrams[idx][1][idx2]
    arr_3[0,] = kmerskipgrams[idx][2][idx2]
    loss = model.train_on_batch([arr_1, arr_2], arr_3)
    #print(i)
    if cnt % 1000 == 0:
        print("Iteration {}, loss={}".format(cnt, loss))
    if cnt % 100000 == 0:
        sim_cb.run_sim()
    if cnt % int(epochs/3) == 0 and cnt != 0:
        ite+=1
        print("Loading ",ite+1,"/ 3 part of data")
        del kmerskipgrams
        kmerskipgrams=generateskipgrams(kmersidx[ite*thirdlength:(ite+1)*thirdlength-1])    
    if cnt % 5000000 == 0:
        model.save_weights('82529sample5000000epochsAsgari.hdf')
model.save_weights('82529sample10000000epochsAsgari.hdf')

Loading  1 / 3 part of data
Iteration 0, loss=0.560081422328949
Nearest to EEE: EDE, EEK, SEE, EED, LEE, EEL, EEV, DED,
Nearest to AGV: VVA, AVL, ALG, AAL, AGA, VAA, LIA, VVV,
Nearest to ALL: ALA, AAL, LAA, AVA, LAE, AVL, VVV, LAL,
Nearest to LGA: AAG, ALG, LVA, GLG, AAL, AIA, LAL, VAG,
Nearest to EEL: ELE, LEE, LLK, ELL, LKE, AKL, KKL, KEL,
Nearest to LAD: AAR, DAL, LAE, LAR, RAA, RAV, LRA, AVA,
Nearest to AAL: LLA, VAA, AAG, LAA, GAV, AVA, AAI, LAG,
Nearest to LGL: AVL, ALS, ALV, LAE, ELA, ALG, AIA, AAL,
Nearest to LAR: LAD, LAE, AER, LRA, DAL, AAR, RAA, AEA,
Nearest to LAE: ELA, DAL, AEL, LRE, AEA, AVE, AVA, VAE,
Nearest to LEE: EEL, LKE, ELE, ELK, KEL, EKL, LLK, EEI,
Nearest to ELA: LAE, AEL, DAL, LRE, LDD, DEL, LDA, LEA,
Nearest to LKE: EEL, ELK, LEE, LKK, KKL, KLK, ELE, LLK,
Nearest to SLS: SVL, LVS, ALV, ASL, AVL, LSE, LTL, LSS,
Nearest to ASL: ELA, ALS, AVL, VSG, AEL, ASA, LDE, GLS,
Nearest to EKL: ELE, ELK, LKE, EEI, LEE, EEL, KKL, KEL,
Iteration 1000, loss=0.24378594756126404

Iteration 154000, loss=0.5273155570030212
Iteration 155000, loss=1.0732581615447998
Iteration 156000, loss=0.43139100074768066
Iteration 157000, loss=1.1242282390594482
Iteration 158000, loss=0.7442158460617065
Iteration 159000, loss=0.21442261338233948
Iteration 160000, loss=0.9465557336807251
Iteration 161000, loss=0.4480169415473938
Iteration 162000, loss=0.7480459809303284
Iteration 163000, loss=1.2831135988235474
Iteration 164000, loss=1.2857208251953125
Iteration 165000, loss=0.8759504556655884
Iteration 166000, loss=0.035704102367162704
Iteration 167000, loss=0.5693531632423401
Iteration 168000, loss=0.5102096796035767
Iteration 169000, loss=0.4480521082878113
Iteration 170000, loss=0.2880578637123108
Iteration 171000, loss=0.9698266983032227
Iteration 172000, loss=0.26934388279914856
Iteration 173000, loss=0.8434114456176758
Iteration 174000, loss=0.1406184285879135
Iteration 175000, loss=0.9112975001335144
Iteration 176000, loss=0.5728023052215576
Iteration 177000, loss=0.8855

Iteration 306000, loss=0.4669933319091797
Iteration 307000, loss=0.17545488476753235
Iteration 308000, loss=0.38767555356025696
Iteration 309000, loss=0.09522221982479095
Iteration 310000, loss=0.9912174344062805
Iteration 311000, loss=0.22418734431266785
Iteration 312000, loss=0.3300698697566986
Iteration 313000, loss=0.47758713364601135
Iteration 314000, loss=1.0035403966903687
Iteration 315000, loss=0.507623016834259
Iteration 316000, loss=0.9236323833465576
Iteration 317000, loss=0.8218334317207336
Iteration 318000, loss=0.6851074695587158
Iteration 319000, loss=0.2090648114681244
Iteration 320000, loss=0.5266060829162598
Iteration 321000, loss=0.5235363841056824
Iteration 322000, loss=0.6703100800514221
Iteration 323000, loss=0.9791621565818787
Iteration 324000, loss=0.025762014091014862
Iteration 325000, loss=0.4225393235683441
Iteration 326000, loss=0.38946717977523804
Iteration 327000, loss=1.1116576194763184
Iteration 328000, loss=0.4256637692451477
Iteration 329000, loss=1.01

Iteration 480000, loss=0.2197171449661255
Iteration 481000, loss=0.6869869232177734
Iteration 482000, loss=0.45099109411239624
Iteration 483000, loss=0.9435986876487732
Iteration 484000, loss=0.924040675163269
Iteration 485000, loss=0.4420691430568695
Iteration 486000, loss=0.7538567781448364
Iteration 487000, loss=0.947034478187561
Iteration 488000, loss=0.8862171173095703
Iteration 489000, loss=0.024540655314922333
Iteration 490000, loss=0.46435874700546265
Iteration 491000, loss=0.5037522912025452
Iteration 492000, loss=0.9443274736404419
Iteration 493000, loss=0.191267728805542
Iteration 494000, loss=0.5377951264381409
Iteration 495000, loss=0.9212459325790405
Iteration 496000, loss=0.6569898724555969
Iteration 497000, loss=0.39453184604644775
Iteration 498000, loss=0.4403340220451355
Iteration 499000, loss=3.8225977420806885
Iteration 500000, loss=0.5068498849868774
Nearest to EEE: EDE, SEE, EEK, EED, LEE, EEV, EEL, EDD,
Nearest to AGV: VVA, ALG, AVL, AGA, AAL, LIA, VAA, TAA,
Near

Iteration 632000, loss=0.9361408948898315
Iteration 633000, loss=0.9652330875396729
Iteration 634000, loss=1.5185370445251465
Iteration 635000, loss=0.8212803602218628
Iteration 636000, loss=0.4210836887359619
Iteration 637000, loss=1.3847284317016602
Iteration 638000, loss=0.5606753826141357
Iteration 639000, loss=3.1277432441711426
Iteration 640000, loss=0.2240138053894043
Iteration 641000, loss=0.4315633475780487
Iteration 642000, loss=0.18823891878128052
Iteration 643000, loss=0.2948179244995117
Iteration 644000, loss=0.4874742031097412
Iteration 645000, loss=1.0629842281341553
Iteration 646000, loss=0.14086121320724487
Iteration 647000, loss=0.32814472913742065
Iteration 648000, loss=0.0025143015664070845
Iteration 649000, loss=0.7078214883804321
Iteration 650000, loss=0.5070481896400452
Iteration 651000, loss=0.4691169261932373
Iteration 652000, loss=0.4546123445034027
Iteration 653000, loss=0.46402910351753235
Iteration 654000, loss=0.9316831827163696
Iteration 655000, loss=1.27

...

Nearest to LAR: LRA, LAE, AER, LAD, DAL, AEA, AAE, ELR,
Nearest to LAE: AVA, DAL, ELA, AEA, EAL, AEL, ADA, LDA,
Nearest to LEE: LKE, EEL, KEL, LLK, ELK, EKL, ELE, LKK,
Nearest to ELA: DAL, LAE, AEL, DEL, LDD, AVE, LDA, VEA,
Nearest to LKE: LKK, KLK, ELK, LLK, KKL, KEL, LEE, LEK,
Nearest to SLS: SVL, ASL, LSE, KAL, LTL, LVS, SLT, ALV,
Nearest to ASL: VSG, ALS, SLT, ASA, GLS, LNG, ELA, VTL,
Nearest to EKL: ELE, KEL, LEE, EEI, EEV, DEI, LLK, KKL,
Iteration 9301000, loss=1.7923303842544556
Iteration 9302000, loss=0.43454623222351074
Iteration 9303000, loss=2.6226376576232724e-05
Iteration 9304000, loss=0.43125858902931213
Iteration 9305000, loss=0.016065817326307297
Iteration 9306000, loss=0.4750487506389618
Iteration 9307000, loss=0.0008503234712406993
Iteration 9308000, loss=0.3690522611141205
Iteration 9309000, loss=0.2197364717721939
Iteration 9310000, loss=0.6366699934005737
Iteration 9311000, loss=0.4777407944202423
Iteration 9312000, loss=0.5576986074447632
Iteration 9313000, loss=0

Iteration 9459000, loss=0.004943431355059147
Iteration 9460000, loss=0.09033612161874771
Iteration 9461000, loss=0.281369149684906
Iteration 9462000, loss=0.7899363040924072
Iteration 9463000, loss=2.0329182147979736
Iteration 9464000, loss=0.010135703720152378
Iteration 9465000, loss=0.517987847328186
Iteration 9466000, loss=0.3337676525115967
Iteration 9467000, loss=0.4142766296863556
Iteration 9468000, loss=0.31460538506507874
Iteration 9469000, loss=0.2813545763492584
Iteration 9470000, loss=0.7081024050712585
Iteration 9471000, loss=1.6882133483886719
Iteration 9472000, loss=2.378804922103882
Iteration 9473000, loss=0.5799367427825928
Iteration 9474000, loss=0.45174354314804077
Iteration 9475000, loss=2.3162808418273926
Iteration 9476000, loss=0.46000581979751587
Iteration 9477000, loss=2.7964823246002197
Iteration 9478000, loss=1.2176768779754639
Iteration 9479000, loss=0.4266418218612671
Iteration 9480000, loss=0.6907023191452026
Iteration 9481000, loss=0.5208905339241028
Iterat

Iteration 9607000, loss=0.46029844880104065
Iteration 9608000, loss=0.7213067412376404
Iteration 9609000, loss=0.06990543007850647
Iteration 9610000, loss=0.3490447700023651
Iteration 9611000, loss=0.00025543858646415174
Iteration 9612000, loss=0.6306291222572327
Iteration 9613000, loss=0.5924279093742371
Iteration 9614000, loss=0.003113402286544442
Iteration 9615000, loss=0.02356070652604103
Iteration 9616000, loss=0.71406489610672
Iteration 9617000, loss=0.29889029264450073
Iteration 9618000, loss=0.2649974226951599
Iteration 9619000, loss=3.1601052284240723
Iteration 9620000, loss=4.063227653503418
Iteration 9621000, loss=0.8771795630455017
Iteration 9622000, loss=0.7045087218284607
Iteration 9623000, loss=0.27271100878715515
Iteration 9624000, loss=6.619068622589111
Iteration 9625000, loss=0.0560634583234787
Iteration 9626000, loss=0.013728726655244827
Iteration 9627000, loss=0.44029390811920166
Iteration 9628000, loss=5.054564952850342
Iteration 9629000, loss=2.6844162940979004
It

Iteration 9776000, loss=0.06278140097856522
Iteration 9777000, loss=0.009913727641105652
Iteration 9778000, loss=0.7294784784317017
Iteration 9779000, loss=0.005035960581153631
Iteration 9780000, loss=0.4629591405391693
Iteration 9781000, loss=0.29519346356391907
Iteration 9782000, loss=0.9075602293014526
Iteration 9783000, loss=0.2095872014760971
Iteration 9784000, loss=0.6496607661247253
Iteration 9785000, loss=0.505623996257782
Iteration 9786000, loss=1.3978142738342285
Iteration 9787000, loss=0.3119886517524719
Iteration 9788000, loss=0.43769049644470215
Iteration 9789000, loss=1.310757040977478
Iteration 9790000, loss=0.4281046986579895
Iteration 9791000, loss=0.07500158995389938
Iteration 9792000, loss=0.39309024810791016
Iteration 9793000, loss=0.15111497044563293
Iteration 9794000, loss=0.9727692604064941
Iteration 9795000, loss=0.5227031111717224
Iteration 9796000, loss=0.03140469640493393
Iteration 9797000, loss=0.8301163911819458
Iteration 9798000, loss=0.1364249289035797
It

Iteration 9925000, loss=3.500519275665283
Iteration 9926000, loss=1.193776249885559
Iteration 9927000, loss=0.15805627405643463
Iteration 9928000, loss=0.9068409204483032
Iteration 9929000, loss=0.4415319561958313
Iteration 9930000, loss=0.14007426798343658
Iteration 9931000, loss=0.0001227930624736473
Iteration 9932000, loss=0.40701910853385925
Iteration 9933000, loss=0.4123241603374481
Iteration 9934000, loss=1.5125787258148193
Iteration 9935000, loss=0.3776432275772095
Iteration 9936000, loss=0.004167466424405575
Iteration 9937000, loss=0.11180278658866882
Iteration 9938000, loss=0.0027837117668241262
Iteration 9939000, loss=1.382317066192627
Iteration 9940000, loss=2.0171871185302734
Iteration 9941000, loss=0.4558243751525879
Iteration 9942000, loss=7.591010093688965
Iteration 9943000, loss=4.246491432189941
Iteration 9944000, loss=0.2150522619485855
Iteration 9945000, loss=0.524698793888092
Iteration 9946000, loss=0.00011754722072510049
Iteration 9947000, loss=0.004576476756483316

## Training Eshan's embedding with SwissProt 2015 data, random sampling

In [28]:
epochs = 5000000
valid_size = 16  # Random set of words to evaluate similarity on.
valid_window = 100 # Only pick dev samples in the head of the distribution.
valid_examples = np.random.choice(valid_window, valid_size, replace=False)
thirdlength = int(len(swissprot)/30)
#ite=0

print("Loading part",ite+1,"/ 30 of data, length of ",thirdlength)
#kmerskipgrams=generateskipgrams(swissprot['Sequence'].iloc[:thirdlength-1].values,threemersidx)

arr_1 = np.zeros((1,))
arr_2 = np.zeros((1,))
arr_3 = np.zeros((1,))
for cnt in range(epochs):
    idx = np.random.randint(0, len(kmerskipgrams)-1)
    while type(kmerskipgrams[idx]) != tuple:
        idx = np.random.randint(0, len(kmerskipgrams)-1)
    idx2 = np.random.randint(0,len(kmerskipgrams[idx][0])-1)
    arr_1[0,] = kmerskipgrams[idx][0][idx2]
    arr_2[0,] = kmerskipgrams[idx][1][idx2]
    arr_3[0,] = kmerskipgrams[idx][2][idx2]
    loss = model.train_on_batch([arr_1, arr_2], arr_3)
    #print(i)
    if cnt % 1000 == 0:
        print("Iteration {}, loss={}".format(cnt, loss))
    if cnt % 100000 == 0:
        sim_cb.run_sim()
    if cnt % int(epochs/15) == 0 and cnt != 0:
        ite+=1
        print("Loading ",ite+1,"/ 30 part of data")
        del kmerskipgrams
        kmerskipgrams=generateskipgrams(swissprot['Sequence'].iloc[ite*thirdlength:(ite+1)*thirdlength-1].values,threemersidx)    
    #if cnt % 5000000 == 0:
        #model.save_weights('swissprot5000000epochsAsgari.hdf')
model.save_weights('swissprot10000000epochsAsgari.hdf')

Loading part 16 / 30 of data, length of  10800
Iteration 0, loss=1.0566415786743164
Nearest to LAD: EAL, LAE, EAA, LRE, ALA, AEL, ADL, ARL,
Nearest to LSS: SSL, SLS, SLT, ASL, LPL, SSA, SLL, LIS,
Nearest to LLS: VLL, SLL, SSL, TLL, LLL, LLD, LSG, VLS,
Nearest to LDL: EAL, LAE, ARL, AEL, RAL, LLQ, LAD, ELA,
Nearest to RLL: LAA, ALA, ALL, VLA, AAL, LAE, ALS, ALV,
Nearest to GAL: GLA, LAL, ALL, AGL, LGA, AVA, AAL, AVL,
Nearest to LAR: LAD, ALA, LAE, ARL, ALV, EAA, AAL, ALS,
Nearest to LLR: LAE, LAL, ALL, VAA, LLE, ELL, LAD, LGL,
Nearest to GGG: GGS, AGA, GAG, AGG, GSG, AAV, ASG, LAA,
Nearest to LLD: ELL, LLE, LSL, SLE, LAE, LLK, LEE, LLN,
Nearest to EEA: EAE, EEV, AAE, AEA, ERL, AEE, AEL, ELE,
Nearest to AAS: ALA, AAG, AAL, SAA, EAL, AGG, LAA, ASA,
Nearest to LAA: ALA, AAL, AAG, ALG, LGA, LAV, AAV, LAL,
Nearest to LSA: ALL, ALA, LAL, AAL, IAA, ALS, LGL, VAA,
Nearest to KLL: LEE, EEL, ELL, LLE, LEK, LLN, EKL, LKE,
Nearest to LLA: LAL, LGL, ALA, AAL, ALL, LAA, AAV, LAG,
Iteration 1000, loss

Iteration 154000, loss=1.0765211582183838
Iteration 155000, loss=0.31982553005218506
Iteration 156000, loss=0.37975743412971497
Iteration 157000, loss=0.19878631830215454
Iteration 158000, loss=0.8588283658027649
Iteration 159000, loss=0.8674832582473755
Iteration 160000, loss=0.43957167863845825
Iteration 161000, loss=0.41174548864364624
Iteration 162000, loss=0.0027959654107689857
Iteration 163000, loss=0.25165992975234985
Iteration 164000, loss=0.7996602058410645
Iteration 165000, loss=0.9850031733512878
Iteration 166000, loss=0.6456142663955688
Iteration 167000, loss=0.4990098178386688
Iteration 168000, loss=0.9929490685462952
Iteration 169000, loss=0.40734824538230896
Iteration 170000, loss=0.4538172483444214
Iteration 171000, loss=0.7232275605201721
Iteration 172000, loss=0.6774521470069885
Iteration 173000, loss=0.7433223128318787
Iteration 174000, loss=0.4430788457393646
Iteration 175000, loss=1.1718047857284546
Iteration 176000, loss=0.7401580810546875
Iteration 177000, loss=0

Iteration 306000, loss=0.3138674795627594
Iteration 307000, loss=0.5742306709289551
Iteration 308000, loss=0.5221030116081238
Iteration 309000, loss=1.0148297548294067
Iteration 310000, loss=0.6322566866874695
Iteration 311000, loss=0.7115058302879333
Iteration 312000, loss=0.7515936493873596
Iteration 313000, loss=0.2797688841819763
Iteration 314000, loss=1.3499433994293213
Iteration 315000, loss=1.2239046096801758
Iteration 316000, loss=0.434425413608551
Iteration 317000, loss=0.22198623418807983
Iteration 318000, loss=0.34062659740448
Iteration 319000, loss=0.8009414076805115
Iteration 320000, loss=1.2527602910995483
Iteration 321000, loss=0.41428813338279724
Iteration 322000, loss=0.34689128398895264
Iteration 323000, loss=0.5286926031112671
Iteration 324000, loss=1.1199498176574707
Iteration 325000, loss=1.1759999990463257
Iteration 326000, loss=1.008187174797058
Iteration 327000, loss=0.4278722405433655
Iteration 328000, loss=0.477649450302124
Iteration 329000, loss=0.40856909751

Iteration 479000, loss=0.8088709712028503
Iteration 480000, loss=0.994045078754425
Iteration 481000, loss=0.43353497982025146
Iteration 482000, loss=1.0310182571411133
Iteration 483000, loss=0.5268542766571045
Iteration 484000, loss=0.9804791808128357
Iteration 485000, loss=0.3142664432525635
Iteration 486000, loss=2.7118959426879883
Iteration 487000, loss=0.4460429549217224
Iteration 488000, loss=0.47364872694015503
Iteration 489000, loss=1.0470476150512695
Iteration 490000, loss=0.12667372822761536
Iteration 491000, loss=0.3087378442287445
Iteration 492000, loss=0.42303889989852905
Iteration 493000, loss=1.2616631984710693
Iteration 494000, loss=0.9334051012992859
Iteration 495000, loss=0.026669736951589584
Iteration 496000, loss=0.5930293202400208
Iteration 497000, loss=0.280862420797348
Iteration 498000, loss=1.0219208002090454
Iteration 499000, loss=1.0488743782043457
Iteration 500000, loss=1.0423855781555176
Nearest to LAD: EAL, LAE, ALA, AAL, EAA, LRE, AEL, ARL,
Nearest to LSS: 

Iteration 631000, loss=0.12229698151350021
Iteration 632000, loss=0.5154257416725159
Iteration 633000, loss=0.5290799736976624
Iteration 634000, loss=0.6207733750343323
Iteration 635000, loss=0.42164382338523865
Iteration 636000, loss=0.34851232171058655
Iteration 637000, loss=0.4293522536754608
Iteration 638000, loss=0.655593991279602
Iteration 639000, loss=0.8944250345230103
Iteration 640000, loss=0.01773160696029663
Iteration 641000, loss=0.2781953513622284
Iteration 642000, loss=1.0700149536132812
Iteration 643000, loss=0.15962840616703033
Iteration 644000, loss=0.40434277057647705
Iteration 645000, loss=0.053604550659656525
Iteration 646000, loss=0.977487325668335
Iteration 647000, loss=1.1141722202301025
Iteration 648000, loss=1.0776087045669556
Iteration 649000, loss=1.1001086235046387
Iteration 650000, loss=0.3064216673374176
Iteration 651000, loss=0.48220181465148926
Iteration 652000, loss=0.4927730858325958
Iteration 653000, loss=0.3405105769634247
Iteration 654000, loss=1.07

...

Iteration 4262000, loss=0.9365075826644897
Iteration 4263000, loss=0.031162390485405922
Iteration 4264000, loss=0.6609997153282166
Iteration 4265000, loss=0.4165477454662323
Iteration 4266000, loss=0.05009251460433006
Iteration 4267000, loss=0.46830832958221436
Iteration 4268000, loss=0.9902704954147339
Iteration 4269000, loss=0.861098051071167
Iteration 4270000, loss=0.367644339799881
Iteration 4271000, loss=0.3778251111507416
Iteration 4272000, loss=0.4697357416152954
Iteration 4273000, loss=0.7834973931312561
Iteration 4274000, loss=0.4794183373451233
Iteration 4275000, loss=1.6632094383239746
Iteration 4276000, loss=1.3287385702133179
Iteration 4277000, loss=0.377375990152359
Iteration 4278000, loss=1.1266520023345947
Iteration 4279000, loss=0.69814532995224
Iteration 4280000, loss=0.9840015172958374
Iteration 4281000, loss=0.9856996536254883
Iteration 4282000, loss=0.711298406124115
Iteration 4283000, loss=0.8914894461631775
Iteration 4284000, loss=0.39944034814834595
Iteration 42

Iteration 4410000, loss=0.34805911779403687
Iteration 4411000, loss=1.0137958526611328
Iteration 4412000, loss=0.4397140443325043
Iteration 4413000, loss=2.651331901550293
Iteration 4414000, loss=0.5067958831787109
Iteration 4415000, loss=0.39124801754951477
Iteration 4416000, loss=0.8026202917098999
Iteration 4417000, loss=0.3927711546421051
Iteration 4418000, loss=1.1378333568572998
Iteration 4419000, loss=1.2854514122009277
Iteration 4420000, loss=0.5854756832122803
Iteration 4421000, loss=0.6250119805335999
Iteration 4422000, loss=1.0436657667160034
Iteration 4423000, loss=0.2849198281764984
Iteration 4424000, loss=0.0882478803396225
Iteration 4425000, loss=0.8317838907241821
Iteration 4426000, loss=0.20329762995243073
Iteration 4427000, loss=0.022034958004951477
Iteration 4428000, loss=0.39819586277008057
Iteration 4429000, loss=0.5726223587989807
Iteration 4430000, loss=1.7313201427459717
Iteration 4431000, loss=0.3595496714115143
Iteration 4432000, loss=1.0508102178573608
Iterat

Iteration 4579000, loss=0.4172252118587494
Iteration 4580000, loss=0.11999809741973877
Iteration 4581000, loss=1.2361334562301636
Iteration 4582000, loss=1.0319658517837524
Iteration 4583000, loss=0.3004246950149536
Iteration 4584000, loss=0.12034197896718979
Iteration 4585000, loss=0.47357407212257385
Iteration 4586000, loss=0.8300855159759521
Iteration 4587000, loss=3.611377239227295
Iteration 4588000, loss=0.21982569992542267
Iteration 4589000, loss=0.8558659553527832
Iteration 4590000, loss=0.6824259161949158
Iteration 4591000, loss=3.592155933380127
Iteration 4592000, loss=0.5145654082298279
Iteration 4593000, loss=2.146578550338745
Iteration 4594000, loss=0.8257642984390259
Iteration 4595000, loss=0.27199456095695496
Iteration 4596000, loss=1.0107989311218262
Iteration 4597000, loss=0.9754540920257568
Iteration 4598000, loss=0.36340954899787903
Iteration 4599000, loss=0.18647870421409607
Iteration 4600000, loss=1.055953025817871
Nearest to LAD: EAL, LAE, ELA, AEL, DAL, ELL, LVG, 

Iteration 4727000, loss=0.6985703706741333
Iteration 4728000, loss=0.7642921209335327
Iteration 4729000, loss=0.49650877714157104
Iteration 4730000, loss=0.9144821763038635
Iteration 4731000, loss=3.9502639770507812
Iteration 4732000, loss=0.5384719371795654
Iteration 4733000, loss=4.043571472167969
Iteration 4734000, loss=0.19508206844329834
Iteration 4735000, loss=0.8204322457313538
Iteration 4736000, loss=1.1132451295852661
Iteration 4737000, loss=1.1410692930221558
Iteration 4738000, loss=0.9726014137268066
Iteration 4739000, loss=0.39998137950897217
Iteration 4740000, loss=0.4917375445365906
Iteration 4741000, loss=1.1243542432785034
Iteration 4742000, loss=1.1472669839859009
Iteration 4743000, loss=1.0509529113769531
Iteration 4744000, loss=0.5335703492164612
Iteration 4745000, loss=0.8423600196838379
Iteration 4746000, loss=1.3860141038894653
Iteration 4747000, loss=0.8521842360496521
Iteration 4748000, loss=0.29047316312789917
Iteration 4749000, loss=0.48953336477279663
Iterati

Iteration 4897000, loss=0.9952328205108643
Iteration 4898000, loss=0.3325263261795044
Iteration 4899000, loss=0.4658544063568115
Iteration 4900000, loss=0.5146633386611938
Nearest to LAD: EAL, LAE, AEL, ELA, DAL, LEA, ELL, ALV,
Nearest to LSS: SSL, SLS, SLE, SLT, LPL, ASL, LLE, LES,
Nearest to LLS: LAL, SLL, VLL, GLL, LSL, ALL, LAS, TLL,
Nearest to LDL: RAL, ARL, ALR, LEL, LRE, EAA, AAE, LAK,
Nearest to RLL: LAA, VLA, LAE, ALL, AAV, AVL, ALS, ALV,
Nearest to GAL: GLA, LAL, ALL, LAA, AVL, AAL, AVA, AGL,
Nearest to LAR: AAR, LAD, LAE, EAA, ARL, LEA, QAL, RAL,
Nearest to LLR: LAE, ALS, LAR, VAA, LAK, RAL, ILA, LLD,
Nearest to GGG: SGG, AGA, AAV, LAA, GAG, GGS, VLA, AGG,
Nearest to LLD: ELL, EEL, LLE, LAE, LEE, LLN, LLK, LER,
Nearest to EEA: AEE, EEV, AKA, EAE, AAE, EEI, ELE, AEA,
Nearest to AAS: ALA, LAA, AGL, AGG, ALS, ASA, EAL, AAG,
Nearest to LAA: ALA, AAL, LAL, AVL, AAV, ALL, AAG, AGL,
Nearest to LSA: EAL, ALS, LAE, ALV, LAD, ARL, VAA, LAL,
Nearest to KLL: LEE, EEL, EKL, LKL, LKK, LLN

## Training random initialized embedding with SwissProt 2015, sequential sampling

In [ ]:
epochs = 1
samplesize = len(swissprot)
valid_size = 16  # Random set of words to evaluate similarity on.
valid_window = 100 # Only pick dev samples in the head of the distribution.
valid_examples = np.random.choice(valid_window, valid_size, replace=False)
chunklength = 1000
#ite=0
losses = 0
#print("Loading part",ite+1,"/",int(samplesize/chunklength), "of data, length of ",samplesize)
#kmerskipgrams=generateskipgrams(swissprot['Sequence'].iloc[:chunklength-1].values,threemersidx)

arr_1 = np.zeros((1,))
arr_2 = np.zeros((1,))
arr_3 = np.zeros((1,))

for epoch in range(epochs):
    for cnt in range(samplesize):
        idx = cnt-chunklength*ite
        if type(kmerskipgrams[idx]) == tuple:
            for idx2 in range(len(kmerskipgrams[idx][0])):
                arr_1[0,] = kmerskipgrams[idx][0][idx2]
                arr_2[0,] = kmerskipgrams[idx][1][idx2]
                arr_3[0,] = kmerskipgrams[idx][2][idx2]
                loss = model.train_on_batch([arr_1, arr_2], arr_3)
                #losses += loss
                if idx2 % 1000 == 0:
                    #print("Iteration {}, loss={}".format(cnt, loss), "Average loss in last 1000 samples", losses/1000)
                    print("Iteration {}, loss={}".format(cnt, loss))
                    losses = 0
        if cnt % 1000 == 0:
            sim_cb.run_sim()
        if cnt % chunklength == 0 and cnt != 0:
            ite+=1
            print("Loading ",ite+1,"/",int(samplesize/chunklength),"part of data")
            del kmerskipgrams
            kmerskipgrams=generateskipgrams(swissprot['Sequence'].iloc[ite*chunklength:(ite+1)*chunklength-1].values,threemersidx)    
        if cnt % samplesize/2 == 0:
            model.save_weights('swissprothalf.hdf')
model.save_weights('swissprot.hdf')


Iteration 0, loss=0.5659402012825012
Iteration 0, loss=0.5835468769073486
Iteration 0, loss=0.7254899740219116
Iteration 0, loss=0.8543121814727783
Nearest to LLL: DRE, LRG, KAQ, TQT, MAV, ALA, RTV, ESL,
Nearest to ELA: FYL, VND, ATH, AKT, GNN, KID, NCI, LPL,
Nearest to TLL: GYV, APR, PRF, WAG, MRY, PRA, RGE, QFV,
Nearest to LAS: YGF, YFR, WQK, PQY, IFQ, ANH, SWN, EHF,
Nearest to LSS: KDY, AAQ, REA, GKE, DGR, EQQ, LEG, ITQ,
Nearest to LAK: AYM, EFI, QAN, VKQ, KSF, GLK, LHQ, SIK,
Nearest to LLA: LQV, ERT, EEY, TID, LKF, YGI, LQF, TNL,
Nearest to ALA: MAV, LSG, YFS, VGY, FIS, VKA, RTL, SMR,
Nearest to AEA: VLE, PVD, LSL, SVE, EHG, FLV, MIM, ACE,
Nearest to ASL: KYT, CGV, PKG, DLD, RAI, TMT, YEY, IKT,
Nearest to LRE: LKI, TEE, VIN, IRH, IAM, RCY, FKV, TYK,
Nearest to LAV: VPS, GEE, VGI, TCH, QST, GDG, PSS, GDR,
Nearest to KLL: GFE, PSV, DSR, GAH, SRS, QGT, IDE, MLF,
Nearest to LGG: VGF, VRQ, ELG, AGG, CSV, GFK, AQE, GLG,
Nearest to LVA: DLF, LDS, VDE, DSV, EKL, SKY, SSR, TFR,
Nearest to L

Iteration 52, loss=1.2634986639022827
Iteration 53, loss=0.1713050901889801
Iteration 53, loss=0.0096889678388834
Iteration 53, loss=0.3904291093349457
Iteration 53, loss=0.009349179454147816
Iteration 54, loss=0.9325254559516907
Iteration 54, loss=0.3926119804382324
Iteration 54, loss=0.0007529706344939768
Iteration 54, loss=0.28462648391723633
Iteration 55, loss=0.42006099224090576
Iteration 55, loss=0.30202263593673706
Iteration 55, loss=0.1400894671678543
Iteration 55, loss=0.37713974714279175
Iteration 56, loss=0.4305509924888611
Iteration 56, loss=0.8694398999214172
Iteration 56, loss=0.010465718805789948
Iteration 57, loss=0.8712602853775024
Iteration 57, loss=0.1281011402606964
Iteration 57, loss=0.9781169891357422
Iteration 57, loss=0.6021333932876587
Iteration 58, loss=0.016827410086989403
Iteration 58, loss=0.1418222337961197
Iteration 58, loss=0.36242321133613586
Iteration 59, loss=12.387036323547363
Iteration 59, loss=0.4180459678173065
Iteration 59, loss=0.163323387503623

Iteration 112, loss=0.6185908317565918
Iteration 112, loss=0.0026680624578148127
Iteration 112, loss=0.7961156368255615
Iteration 112, loss=0.8498910665512085
Iteration 113, loss=0.7206984162330627
Iteration 113, loss=0.8077594637870789
Iteration 113, loss=0.6058177351951599
Iteration 113, loss=0.018283739686012268
Iteration 113, loss=0.9282070398330688
Iteration 114, loss=1.0587270259857178
Iteration 114, loss=0.8145214319229126
Iteration 114, loss=0.5513955354690552
Iteration 114, loss=0.6148942708969116
Iteration 114, loss=0.5336239337921143
Iteration 115, loss=0.0052235424518585205
Iteration 115, loss=0.9986786842346191
Iteration 115, loss=0.8044248819351196
Iteration 115, loss=0.5455598831176758
Iteration 116, loss=0.5452888607978821
Iteration 116, loss=0.6190677285194397
Iteration 116, loss=0.8465803861618042
Iteration 116, loss=0.13985197246074677
Iteration 117, loss=0.7489850521087646
Iteration 117, loss=0.87183678150177
Iteration 117, loss=0.328921914100647
Iteration 117, loss

Iteration 166, loss=0.39602193236351013
Iteration 166, loss=0.43234124779701233
Iteration 167, loss=0.5508823990821838
Iteration 167, loss=0.8057112097740173
Iteration 167, loss=0.16731414198875427
Iteration 168, loss=0.4892611503601074
Iteration 168, loss=0.33186858892440796
Iteration 168, loss=0.2923237681388855
Iteration 168, loss=0.004718450363725424
Iteration 169, loss=0.4372650384902954
Iteration 169, loss=0.3624447286128998
Iteration 169, loss=0.9636645913124084
Iteration 170, loss=1.4768178462982178
Iteration 170, loss=0.933722734451294
Iteration 170, loss=0.3477878272533417
Iteration 170, loss=0.16483156383037567
Iteration 171, loss=0.24811524152755737
Iteration 171, loss=1.0225718021392822
Iteration 171, loss=0.9092229604721069
Iteration 171, loss=0.8715794682502747
Iteration 172, loss=0.5467170476913452
Iteration 172, loss=0.1813552975654602
Iteration 172, loss=0.5397467613220215
Iteration 172, loss=1.2997268438339233
Iteration 173, loss=0.40779781341552734
Iteration 173, lo

Iteration 222, loss=0.26023364067077637
Iteration 222, loss=0.004341835621744394
Iteration 223, loss=0.0281990934163332
Iteration 223, loss=0.008992995135486126
Iteration 223, loss=6.885312557220459
Iteration 224, loss=1.3531196117401123
Iteration 224, loss=0.282797247171402
Iteration 224, loss=1.421236276626587
Iteration 224, loss=0.8852584362030029
Iteration 225, loss=0.7125771045684814
Iteration 225, loss=1.2472443580627441
Iteration 225, loss=0.01679200865328312
Iteration 225, loss=0.548809826374054
Iteration 226, loss=2.168588399887085
Iteration 226, loss=0.38872814178466797
Iteration 226, loss=0.25272777676582336
Iteration 226, loss=1.08676278591156
Iteration 227, loss=1.1090683937072754
Iteration 227, loss=0.44126906991004944
Iteration 227, loss=0.4413825273513794
Iteration 228, loss=0.435401976108551
Iteration 228, loss=0.482329785823822
Iteration 228, loss=0.5240804553031921
Iteration 228, loss=0.02270117588341236
Iteration 229, loss=0.7715977430343628
Iteration 229, loss=0.53

...

Iteration 18833, loss=0.002005918649956584
Iteration 18833, loss=0.05557188391685486
Iteration 18834, loss=0.0008092217613011599
Iteration 18834, loss=0.02343512512743473
Iteration 18834, loss=1.2043366432189941
Iteration 18834, loss=7.89904260635376
Iteration 18834, loss=0.07461277395486832
Iteration 18835, loss=0.08431949466466904
Iteration 18835, loss=1.5543633699417114
Iteration 18835, loss=0.025026442483067513
Iteration 18835, loss=0.00045778637286275625
Iteration 18835, loss=0.0005120158311910927
Iteration 18836, loss=0.136647030711174
Iteration 18836, loss=1.192093321833454e-07
Iteration 18836, loss=0.02916596084833145
Iteration 18836, loss=8.905329741537571e-05
Iteration 18836, loss=1.7000926733016968
Iteration 18837, loss=0.002350368769839406
Iteration 18837, loss=0.0001221969723701477
Iteration 18837, loss=2.3672800064086914
Iteration 18837, loss=0.0009665389079600573
Iteration 18837, loss=3.5762843708653236e-06
Iteration 18837, loss=15.942384719848633
Iteration 18838, loss=2

Iteration 18872, loss=4.1843326471280307e-05
Iteration 18872, loss=6.640175706706941e-05
Iteration 18872, loss=4.155796051025391
Iteration 18872, loss=5.162824630737305
Iteration 18873, loss=1.192034363746643
Iteration 18873, loss=1.192093321833454e-07
Iteration 18873, loss=0.0646389052271843
Iteration 18873, loss=13.052013397216797
Iteration 18873, loss=0.0002985036699101329
Iteration 18873, loss=1.500320315361023
Iteration 18874, loss=2.100712776184082
Iteration 18874, loss=0.034526702016592026
Iteration 18874, loss=0.977123498916626
Iteration 18874, loss=0.7711087465286255
Iteration 18874, loss=0.00031237711664289236
Iteration 18875, loss=2.739574432373047
Iteration 18875, loss=8.242316246032715
Iteration 18875, loss=8.017333984375
Iteration 18875, loss=0.19964957237243652
Iteration 18875, loss=0.03474951535463333
Iteration 18876, loss=11.864847183227539
Iteration 18876, loss=0.030041135847568512
Iteration 18876, loss=1.192093321833454e-07
Iteration 18876, loss=3.814704541582614e-06

Iteration 18906, loss=0.20863327383995056
Iteration 18906, loss=0.030404549092054367
Iteration 18906, loss=6.561122427228838e-05
Iteration 18906, loss=0.004709217697381973
Iteration 18907, loss=0.004393917508423328
Iteration 18907, loss=13.303328514099121
Iteration 18907, loss=0.018054181709885597
Iteration 18907, loss=8.175792754627764e-05
Iteration 18908, loss=1.1682582226058003e-05
Iteration 18908, loss=0.01071572583168745
Iteration 18908, loss=2.063776969909668
Iteration 18908, loss=0.019853657111525536
Iteration 18908, loss=0.0063748531974852085
Iteration 18908, loss=0.4597640633583069
Iteration 18909, loss=4.911544965580106e-05
Iteration 18909, loss=0.12178892642259598
Iteration 18909, loss=1.192093321833454e-07
Iteration 18909, loss=5.96046561440744e-07
Iteration 18909, loss=0.007289026863873005
Iteration 18910, loss=3.5762778338721546e-07
Iteration 18910, loss=0.5264933705329895
Iteration 18910, loss=4.974453926086426
Iteration 18910, loss=0.0013907082611694932
Iteration 18911,

Iteration 18943, loss=0.019165698438882828
Iteration 18943, loss=0.20810721814632416
Iteration 18943, loss=8.953014184953645e-05
Iteration 18943, loss=0.008625198155641556
Iteration 18943, loss=9.334518108516932e-05
Iteration 18944, loss=4.328208923339844
Iteration 18944, loss=4.285678386688232
Iteration 18944, loss=1.192093321833454e-07
Iteration 18944, loss=5.909713268280029
Iteration 18944, loss=0.3013079762458801
Iteration 18945, loss=2.2411588361137547e-05
Iteration 18945, loss=0.11920677125453949
Iteration 18945, loss=0.015437338501214981
Iteration 18945, loss=0.040026914328336716
Iteration 18945, loss=1.0789079169626348e-05
Iteration 18945, loss=1.90735113392293e-06
Iteration 18946, loss=5.801201820373535
Iteration 18946, loss=6.716916084289551
Iteration 18946, loss=0.28304705023765564
Iteration 18946, loss=5.974398136138916
Iteration 18946, loss=0.18017515540122986
Iteration 18946, loss=5.96046561440744e-07
Iteration 18947, loss=0.0003721214015968144
Iteration 18947, loss=0.505

Iteration 18978, loss=0.045145340263843536
Iteration 18978, loss=3.7005715370178223
Iteration 18978, loss=0.0036058062687516212
Iteration 18978, loss=3.4804224967956543
Iteration 18978, loss=0.0434580072760582
Iteration 18978, loss=5.716886520385742
Iteration 18979, loss=0.2240932434797287
Iteration 18979, loss=2.475862741470337
Iteration 18979, loss=1.0000001537946446e-07
Iteration 18979, loss=0.012465300969779491
Iteration 18979, loss=0.7263646721839905
Iteration 18980, loss=0.2022627294063568
Iteration 18980, loss=0.030394291505217552
Iteration 18980, loss=0.9111524820327759
Iteration 18980, loss=1.192093321833454e-07
Iteration 18980, loss=2.084606647491455
Iteration 18981, loss=0.06496196985244751
Iteration 18981, loss=0.12965995073318481
Iteration 18981, loss=0.04656267166137695
Iteration 18981, loss=0.0002348103153053671
Iteration 18981, loss=0.3476618528366089
Iteration 18981, loss=0.6460245847702026
Iteration 18982, loss=1.0000001537946446e-07
Iteration 18982, loss=1.2071259021

In [25]:
embeddingweights = model.layers[2].get_weights()[0]

def protvec(kmersdict, seq, embeddingweights):
    #Convert seq to three lists of kmers 
    kmerlist = kmerlists(seq) 
    kmerlist = [j for i in kmerlist for j in i]
    #Convert center kmers to their vector representations
    kmersvec = [0]*100
    for kmer in kmerlist:
        try:
            kmersvec = np.add(kmersvec,embeddingweights[kmersdict[kmer]])
        except:
            kmersvec = np.add(kmersvec,embeddingweights[kmersdict['<unk>']])
    return kmersvec

def formatprotvecs(protvecs):
    protfeatures = []
    for i in range(100):
        protfeatures.append([vec[i] for vec in protvecs])
    protfeatures = np.array(protfeatures).reshape(len(protvecs),len(protfeatures))
    return protfeatures

def formatprotvecsnormalized(protvecs):
    protfeatures = []
    for i in range(100):
        tempvec = [vec[i] for vec in protvecs]
        mean = np.mean(tempvec)
        var = np.var(tempvec)
        protfeatures.append([(vec[i]-mean)/var for vec in protvecs])
    protfeatures = np.array(protfeatures).reshape(len(protvecs),len(protfeatures))
    return protfeatures

In [ ]:
#protvecs = []
samplestovec = 38457
for i in range(7758,samplestovec):
    print("Processing protein #",i,"/",len(table))
    if type(table['Protein'][i]) != float:
        protvecs.append(protvec(table['Protein'][i]))
    else: 
        protvecs.append('nan')

In [ ]:
protvecs = Parallel(n_jobs=num_cores)(delayed(protvec)(3mersindex, seq, embeddingweights) for seq in table['Protein'])

In [ ]:
#t-SNE visualization
kmervecs_embedded = TSNE(n_components = 2).fit_transform(protvecs)
table['x-tsne'] = kmervecs_embedded[:,0]
table['y-tsne'] = kmervecs_embedded[:,1]

labels = [lab[:3] for lab in tablesm['Type']]
tablesm['labels'] = labels

from ggplot import *
chart = ggplot( tablesm.loc[tablesm['labels']!='UNS'], aes(x='x-tsne', y='y-tsne', color='labels') ) \
        + geom_point(size=75,alpha=0.8) \
        + ggtitle("Amino Acid Embedding Representation of Proteins: t-SNE Visualization")
chart

## Second Attempt: 80000/115000 kmer sequences training set, 1000000 epochs, 1000 samples visualization 

In [ ]:
from ggplot import *
chart = ggplot( tablesm.loc[tablesm['labels']!='UNS'], aes(x='x-tsne', y='y-tsne', color='labels') ) \
        + geom_point(size=75,alpha=0.8) \
        + ggtitle("Amino Acid Embedding Representation of Proteins: t-SNE Visualization")
chart

In [ ]:
tablesm.loc[tablesm['y-tsne'] == max(tablesm['y-tsne'])]

In [ ]:
tablesm = tablesm.drop(tablesm.index[775])

## Trained embedding matrix from Asgari 2015

Source: http://journals.plos.org/plosone/article?id=10.1371/journal.pone.0141287  
Embedding: https://github.com/ehsanasgari/Deep-Proteomics

3-mer embedding trained with 324,018 protein sequences obtained from SwissProt

In [22]:
def protvec(kmersdict, seq, embeddingweights):
    #Convert seq to three lists of kmers 
    kmerlist = kmerlists(seq) 
    kmerlist = [j for i in kmerlist for j in i]
    #Convert center kmers to their vector representations
    kmersvec = [0]*100
    for kmer in kmerlist:
        try:
            kmersvec = np.add(kmersvec,embeddingweights[kmersdict[kmer]])
        except:
            kmersvec = np.add(kmersvec,embeddingweights[kmersdict['<unk>']])
    return kmersvec

In [ ]:
embeddingweights = model.layers[2].get_weights()[0]
ehsanProtVecs = Parallel(n_jobs=num_cores)(delayed(protvec)(threemersidx, seq, embeddingweights) for seq in table['Protein'])

In [ ]:
kmervecs_embedded = TSNE(n_components = 2).fit_transform(ehsanProtVecs)

In [ ]:
tablesm = table[:1000]
tablesm['x-tsne'] = kmervecs_embedded[:,0]
tablesm['y-tsne'] = kmervecs_embedded[:,1]
funclabels = [lab[:3] for lab in tablesm['Type']]
tablesm['labels'] = funclabels

from ggplot import *
chart = ggplot( tablesm.loc[tablesm['labels']!='UNS'], aes(x='x-tsne', y='y-tsne', color='labels') ) \
        + geom_point(size=75,alpha=0.8) \
        + ggtitle("Amino Acid Embedding Representation of Proteins: t-SNE Visualization")
chart

## Train Asgari 2015 initial weights embedding with phage proteins

In [ ]:
kmersfreqsorted = threemers
kmersdict = {}
for i,kmer in enumerate(kmersfreqsorted):
    kmersdict[kmer] = i
#
kmersindex = []
for seq in kmers:
    temp = []
    for kmer in seq:
        try:
            temp.append(kmersdict[kmer])
        except:
            temp.append(kmersdict['<unk>'])
    kmersindex.append(temp)

In [ ]:
len(results[0][2])

In [69]:
# create some input variables
input_target = Input((1,))
input_context = Input((1,))
vector_dim = 100
vocabsize = len(threemers)

embedding = Embedding(vocabsize, vector_dim, input_length=1, name='embedding')
embedding.build((None,))
embedding.set_weights(np.array([embeddingMat]))

target = embedding(input_target)
target = Reshape((vector_dim, 1))(target)
context = embedding(input_context)
context = Reshape((vector_dim, 1))(context)

# setup a cosine similarity operation which will be output in a secondary model
similarity = merge([target, context], mode='cos', dot_axes=0)

# now perform the dot product operation to get a similarity measure
dot_product = merge([target, context], mode='dot', dot_axes=1)
dot_product = Reshape((1,))(dot_product)
# add the sigmoid output layer
output = Dense(1, activation='sigmoid')(dot_product)

# create the primary training model
model = Model(input=[input_target, input_context], output=output)
model.compile(loss='binary_crossentropy', optimizer='rmsprop')

# create a secondary validation model to run our similarity checks during training
validation_model = Model(input=[input_target, input_context], output=similarity)

#model.load_weights("first_training.hd5")
model.summary()

____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
input_3 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
input_4 (InputLayer)             (None, 1)             0                                            
____________________________________________________________________________________________________
embedding (Embedding)            (None, 1, 100)        904800      input_3[0][0]                    
                                                                   input_4[0][0]                    
____________________________________________________________________________________________________
reshape_4 (Reshape)              (None, 100, 1)        0           embedding[0][0]         

c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:17: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\keras\legacy\layers.py:458: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:20: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
c:\programdata\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:26: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=[<tf.Tenso..., outputs=Tensor("de...)`
c:\programdata\anaconda3\envs\tensorflow\lib\site-pack

In [ ]:
reverse_dictionary = kmersfreqsorted
vocab_size = vocabsize
class SimilarityCallback:
    def run_sim(self):
        for i in range(valid_size):
            valid_word = reverse_dictionary[valid_examples[i]]
            top_k = 8  # number of nearest neighbors
            sim = self._get_sim(valid_examples[i])
            nearest = (-sim).argsort()[1:top_k + 1]
            log_str = 'Nearest to %s:' % valid_word
            for k in range(top_k):
                close_word = reverse_dictionary[nearest[k]]
                log_str = '%s %s,' % (log_str, close_word)
            print(log_str)

    @staticmethod
    def _get_sim(valid_word_idx):
        sim = np.zeros((vocab_size,))
        in_arr1 = np.zeros((1,))
        in_arr2 = np.zeros((1,))
        for i in range(vocab_size):
            in_arr1[0,] = valid_word_idx
            in_arr2[0,] = i
            out = validation_model.predict_on_batch([in_arr1, in_arr2])
            sim[i] = out
        return sim
sim_cb = SimilarityCallback()

In [ ]:
epochs = 10000000
valid_size = 16
valid_window = 100
valid_examples = np.random.choice(valid_window, valid_size, replace=False)
kmerskipgrams=generateskipgrams(kmersidx[:int(len(kmersidx)/3)])
arr_1 = np.zeros((1,))
arr_2 = np.zeros((1,))
arr_3 = np.zeros((1,))
for cnt in range(epochs):
    idx = np.random.randint(0, len(results)-1)
    while type(results[idx]) != tuple:
        idx = np.random.randint(0, len(results)-1)
    idx2 = np.random.randint(0,len(results[idx][0])-1)
    arr_1[0,] = results[idx][0][idx2]
    arr_2[0,] = results[idx][1][idx2]
    arr_3[0,] = results[idx][2][idx2]
    loss = model.train_on_batch([arr_1, arr_2], arr_3)
    #print(i)
    if cnt % 1000 == 0:
        print("Iteration {}, loss={}".format(cnt, loss))
    if cnt % 100000 == 0:
        sim_cb.run_sim()
    if cnt % 5000000 == 0:
        model.save_weights('38420sample5000000epochsAsgari.hdf')
model.save_weights('38420sample10000000epochsAsgari.hdf')

In [ ]:
epochs = 1000000
valid_size = 16
valid_window = 100
valid_examples = np.random.choice(valid_window, valid_size, replace=False)

arr_1 = np.zeros((1,))
arr_2 = np.zeros((1,))
arr_3 = np.zeros((1,))
for cnt in range(epochs):
    idx = np.random.randint(0, len(labels)-1)
    arr_1[0,] = word_target[idx]
    arr_2[0,] = word_context[idx]
    arr_3[0,] = labels[idx]
    loss = model.train_on_batch([arr_1, arr_2], arr_3)
    #print(i)
    if cnt % 1000 == 0:
        print("Iteration {}, loss={}".format(cnt, loss))
    if cnt % 100000 == 0:
        sim_cb.run_sim()
    if cnt % 5000000 == 0:
        model.save_weights('1to80000sample5000000epochsAsgari.hdf')
model.save_weights('1to80000sample1100000epochsAsgari.hdf')

### Initial Asgari Embedding
Nearest to ALV: ALA, ALI, GVL, ATL, LVL, AVL, ALL, LLA,  
Nearest to SLS: SMS, LSS, SSE, SIS, SES, SAS, SSS, SQS,  
Nearest to VLA: FAY, ILA, PNK, VLV, RSI, AIL, SIL, LGG,  
Nearest to LLD: RML, DVL, GHV, LID, LLE, DFA, ILD, TLE,  
Nearest to LAS: LTW, QPV, IAS, MAS, XTW, LLT, IGQ, IGG,  
Nearest to ALR: FAD, RVR, AVR, ARL, LRI, AEL, NVF, LAE,  
Nearest to AAS: ASA, AAA, SAA, AVS, PAA, AAG, AAT, AAP,  
Nearest to SSS: SST, SAS, SSA, PSS, SPS, ASS, SSP, TSS,   
Nearest to EAA: AAE, AEA, KAA, KAE, EAE, AEL, AEE, DAA,   
Nearest to GGG: GGS, GGY, GYG, AGG, SGG, GGA, GGN, GFG,   
Nearest to LLL: MLL, LLV, FLL, VLL, CLL, LVL, LLI, CLW,   
Nearest to LAK: IAK, EKA, GMH, KLA, KNH, VLK, VAK, QKA,  
Nearest to LAR: ARL, AAR, AVR, LAD, LAE, ARA, RLA, AEL,  
Nearest to GAA: GAI, AAG, SAA, GAV, LVV, QMD, MIT, AAA,  
Nearest to LLK: LIK, ILK, KLK, ILE, IIK, QKI, SLK, KQI,  
Nearest to ALE: EAL, DAE, LAE, TLQ, ALD, GEM, QAR, EAA,  

### 500000 Epochs training with 26666 phage proteins on Asgari Embedding
Nearest to ALV: ALA, AVL, ALL, AAL, ALI, LLA, GVL, ALS,  
Nearest to SLS: SIS, SMS, SSE, VSS, SST, NSS, SSD, LSS,  
Nearest to VLA: AAL, LGG, ALA, LAA, VLV, AVL, VAA, VVG,  
Nearest to LLD: ELT, ELL, EAL, LAE, VLE, DLA, ELV, LDD,  
Nearest to LAS: LAA, IAS, ALS, AAL, ASA, AVS, LAG, AAS,  
Nearest to ALR: LAE, AAG, AVR, AEL, DVA, ELV, ALD, ALA,  
Nearest to AAS: ASA, SAA, AAT, AAG, AAV, AVS, LAA, SAT,  
Nearest to SSS: SST, PSS, TSS, SQS, ASS, SSP, SPS, NSS,  
Nearest to EAA: AAE, AEA, KAA, LAE, AEL, AAL, EAL, VEA,  
Nearest to GGG: GGS, SGG, AGG, GGA, GGN, GGY, NGG, GSG,  
Nearest to LLL: LLV, YLL, LAL, FLL, LLI, LLA, VLL, LSL,  
Nearest to LAK: IAK, EAL, LSK, VLK, KLA, KLV, AEL, EKA,  
Nearest to LAR: AVR, AAL, LAD, ALA, LAE, AEL, AAG, VDA,  
Nearest to GAA: AAG, GAV, AGG, SAA, VAA, AAV, GAI, AVA,  
Nearest to LLK: ILE, SLK, LIK, LSK, KKL, ESI, KFI, IKQ,  
Nearest to ALE: EAL, AEL, LAE, AEI, EAA, ELA, LKA, ALK,  

### 900000 Epochs training with 26666 phage proteins on Asgari Embedding
Nearest to ALV: ALA, AVL, AAL, AEL, AIA, LAD, LAT, LTA,  
Nearest to SLS: SIS, SSE, LSS, NSS, LSE, SAS, SSA, SST,  
Nearest to VLA: ALA, AAL, VAA, LAA, DAV, LGG, AAE, AVA,  
Nearest to LLD: LDD, LAD, ELT, ELL, LAE, EAL, ELA, ALE,  
Nearest to LAS: ASA, VAA, LAA, LDD, AVS, TVA, AAL, ELA,  
Nearest to ALR: AVR, LAE, RAL, ALA, AAG, AEL, ALD, LAA,  
Nearest to AAS: ASA, AAG, VAA, LAA, AAT, SAA, SAT, AVS,  
Nearest to SSS: SST, TSS, SAS, PSS, STS, ASS, SSN, SGS,  
Nearest to EAA: AAE, AAL, AEA, AEL, DAV, AAG, DAA, ALA,  
Nearest to GGG: GGS, AGG, SGG, GGA, GSG, GGN, AGA, NGG,  
Nearest to LLL: LLV, LLA, LVL, LAL, LSL, VLL, LTL, ISL,  
Nearest to LAK: IAK, KLA, LSK, VLK, AEL, ELL, ALK, LAE,  
Nearest to LAR: LAE, LAD, AEL, ALA, AAG, AVR, VAA, AAL,  
Nearest to GAA: AAG, AVA, AGG, VAA, AGA, ALA, GAV, GDA,  
Nearest to LLK: ILE, EEL, ELN, VLK, LES, SLK, KKL, LSK,  
Nearest to ALE: AEL, ELA, LAE, ELT, ALK, ALD, DAV, LAD,  
    
### 900000 Epochs training with 26666 phage proteins on random initial weights
Nearest to VGG: HHE, CLF, WAF, HEK, YVY, NRA, IDN, NVL,  
Nearest to ATG: LEE, HRW, VKN, PTI, VKA, HRQ, RST, ANK,  
Nearest to GSG: AIV, FED, LSG, RRL, DWI, CNE, DLI, TVT,  
Nearest to GGT: DMV, FCE, VGR, FLI, GEQ, QAC, PGD, YKT,  
Nearest to ARA: NQH, LRD, AKV, IVK, QLP, LRE, KTD, ART,  
Nearest to LVA: FRF, ENI, YHV, GVR, NYY, ECA, HRG, QNQ,  
Nearest to EAL: RMD, QQG, LYH, WLD, KDT, TMW, LAL, DDE,  
Nearest to VLA: YLN, VTW, HHN, DDE, NRY, LRD, STM, WKV,  
Nearest to ALT: PAL, RLT, QNR, DVA, YMY, CAD, MTQ, IQL,  
Nearest to AGL: PWL, KVE, PII, KMW, IWR, VYA, WFD, VPW,  
Nearest to ALA: TCN, LGL, RWI, CLL, GAR, GGR, QGT, KEP,  
Nearest to LLA: TRY, HII, NGM, FWM, RWI, FPF, LDK, RDS,  
Nearest to GLA: WNR, QRG, FSQ, GMY, IVV, NWK, NHV, QRS,  
Nearest to AAE: THN, YAK, WHA, VVM, SCC, ATA, VSD, MPC,  
Nearest to GGV: QRT, AAQ, VSV, EFN, LCX, RRE, AWQ, WAN,  
Nearest to SGA: AEE, FPH, QSE, RAA, DFK, KND, YNL, WCY,  

In [ ]:
tablesm = table[:1000]
tablesm['x-tsne'] = kmervecs_embedded[:,0]
tablesm['y-tsne'] = kmervecs_embedded[:,1]
labels = [lab[:3] for lab in tablesm['Type']]
tablesm['labels'] = labels

from ggplot import *
chart = ggplot( tablesm.loc[tablesm['labels']!='UNS'], aes(x='x-tsne', y='y-tsne', color='labels') ) \
        + geom_point(size=75,alpha=0.8) \
        + ggtitle("Amino Acid Embedding Representation of Proteins: t-SNE Visualization")
chart

In [ ]:
tablesm = table[:1000]
tablesm['x-tsne'] = kmervecs_embedded[:,0]
tablesm['y-tsne'] = kmervecs_embedded[:,1]
funclabels = [lab[:3] for lab in tablesm['Type']]
tablesm['labels'] = funclabels

from ggplot import *
chart = ggplot( tablesm.loc[tablesm['labels']!='UNS'], aes(x='x-tsne', y='y-tsne', color='labels') ) \
        + geom_point(size=75,alpha=0.8) \
        + ggtitle("Amino Acid Embedding Representation of Proteins: t-SNE Visualization")
chart

## Classification of Protein Function Category

In [ ]:
funclabels = [lab[:3] for lab in table['Type']]
table['labels'] = funclabels
table = table.loc[table['labels'] != 'HYP']
table = table.loc[table['labels'] != 'UNS']

In [ ]:
table['ProtVecs'] = ehsanProtVecs

In [ ]:
table['x-tsne'] = kmervecs_embedded[:,0]
table['y-tsne'] = kmervecs_embedded[:,1]

from ggplot import *
chart = ggplot( tablesm.loc[tablesm['labels']!='UNS'], aes(x='x-tsne', y='y-tsne', color='labels') ) \
        + geom_point(size=75,alpha=0.8) \
        + ggtitle("Amino Acid Embedding Representation of Proteins: t-SNE Visualization")
chart

In [ ]:
set(funclabels)

In [ ]:
funccats = ['ASS','EVA','INF','INT','LYS','PAC','REG','REP','tRN']
labelsonehot = []
funclabels = [lab[:3] for lab in table['Type']]
for lab in funclabels:
    temp = [0]*len(funccats)
    temp[funccats.index(lab)] = 1
    labelsonehot.append(temp)
table['LabelOneHot'] = labelsonehot

In [ ]:
from sklearn.preprocessing import LabelBinarizer
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier, ExtraTreesClassifier
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB, MultinomialNB, BernoulliNB
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix, classification_report,log_loss
from sklearn.model_selection import cross_val_score
from scipy.ndimage.measurements import center_of_mass, label
from skimage.measure import regionprops
from sklearn.cross_validation import ShuffleSplit
from sklearn.grid_search import GridSearchCV
from sklearn.metrics import roc_curve, auc, precision_recall_curve, average_precision_score
from scipy.stats import percentileofscore

In [ ]:
lb = LabelBinarizer()
binlab=lb.fit_transform(table['labels'])

In [ ]:
n_splits=10
kfold=StratifiedKFold(n_splits=n_splits, shuffle=True)

models=[RandomForestClassifier(),
        GradientBoostingClassifier(),]
name=["Random Forest", "Gradient Boosting"]

predictedmodels={}

for nm, clf in zip(name[:-1], models[:-1]):
    print(nm)
    predicted=[]
    for train,test in kfold.split(featuretable,binlab[:,0]):
    scores=cross_val_score(clf,featuretable, binlab, cv=StratifiedKFold(n_splits=n_splits, shuffle=True), n_jobs=-1, scoring='neg_log_loss')
    print("Cross-validated logloss",-np.mean(scores))
    print("---------------------------------------")



In [22]:
def formatprotvecs(protvecs):
    protfeatures = []
    for i in range(100):
        protfeatures.append([vec[i] for vec in protvecs])
    protfeatures = np.array(protfeatures).reshape(len(protvecs),len(protfeatures))
    return protfeatures

def formatprotvecsnormalized(protvecs):
    protfeatures = []
    for i in range(100):
        tempvec = [vec[i] for vec in protvecs]
        mean = np.mean(tempvec)
        var = np.var(tempvec)
        protfeatures.append([(vec[i]-mean)/var for vec in protvecs])
    protfeatures = np.array(protfeatures).reshape(len(protvecs),len(protfeatures))
    return protfeatures

In [ ]:
clf.fit(featuretable, binlab)

In [ ]:
featuretable = pd.DataFrame(np.array(protfeatures).reshape(9173,100))

In [ ]:
#Binary classification of single function
intsamples = table.loc[table['labels']=='INF']
intsamples['binarylabel'] = [1]*len(intsamples)
nonint = table.loc[table['labels'] != 'INF']
nonint['binarylabel'] = [0]*len(nonint)
intsamples = intsamples.append(nonint.sample(frac=len(intsamples)/len(nonint)))
intsamples = intsamples.sample(frac=1)

In [ ]:
features = formatprotvecs(intsamples['ProtVecs'].values)


In [ ]:
models=[LogisticRegression(C=0.1),
        RandomForestClassifier(),
        GradientBoostingClassifier(),
    SVC(C=0.02,kernel='rbf', probability=True)]
name=["Logistic Regression","Random Forest", "Gradient Boosting","SVM rbf kernel"]

predictedmodels={}

for nm, clf in zip(name, models):
    print(nm)
    scores=cross_val_score(clf,features, intsamples['binarylabel'], cv=StratifiedKFold(n_splits=n_splits, shuffle=True), n_jobs=-1, scoring='neg_log_loss')
    print("Cross-validated logloss",-np.mean(scores))
    print("---------------------------------------")
    



In [ ]:
import matplotlib.pyplot as plt

def BinaryClassification(x,y):
    n_splits=10
    kfold=StratifiedKFold(n_splits=n_splits, shuffle=True)
    models=[LogisticRegression(C=0.1),
            RandomForestClassifier(),
            GradientBoostingClassifier(),
        SVC(C=1,kernel='rbf')]
    name=["Logistic Regression", "Random Forest", "Gradient Boosting", "SVM with rbf kernel"]

    predictedmodels={}

    for nm, clf in zip(name[-1:], models[-1:]):
        print(nm)
        predicted=[]
        labelcv=[]
        for train,test in kfold.split(x, y):
            clf.fit(x[train],y[train])
            predicted.append(clf.predict(x[test]))
            labelcv.append(y[test])
        #scores=cross_val_score(clf,x, y, cv=StratifiedKFold(n_splits=n_splits, shuffle=True), n_jobs=-1, scoring='neg_log_loss')
        predicted=np.concatenate(np.array(predicted),axis=0)
        labelcv=np.concatenate(np.array(labelcv),axis=0)
        predictedmodels[nm]=predicted
        #roc=roc_curve(labelcv,predicted)
        #print("Average precision score:", average_precision_score(labelcv,predicted))
        #print("Area under curve:", auc(roc[0],roc[1]))
        #plt.plot(roc[0],roc[1])
        #print(-scores)
        print(classification_report(labelcv,predicted))
        print(confusion_matrix(labelcv,predicted))
        print("Cross-validated logloss",-np.mean(scores))
        print("---------------------------------------")
        #plt.plot(rocrandom[0],rocrandom[1])
    #plt.title('ROC')
    #plt.ylabel('TPrate')
    #plt.xlabel('FPrate')
    #plt.legend(name)
    #plt.savefig("clfroccomparison.png",dpi=300)
    #plt.show()

In [ ]:
#Set up accuracy, sensitivty, specificity as evaluation scorews
#Normalize features
#Try Asgari 2015 initial weights
#Try regularization


## Replicate Asgari 2015 Protein family classification results

In [5]:
swissprot = pd.read_csv("family_classification_metadata.tab", sep='\t')
swissprot['Sequence'] = pd.read_csv("family_classification_sequences.tab", sep='\t')

In [ ]:
swissprot.loc[swissprot['FamilyDescription'] == '50S ribosome-binding GTPase']

In [ ]:
del swissprotseq

In [ ]:
concordance = [table.iloc[i] for i in range(len(table)) if table['Protein'].iloc[i] in swissprot['Sequence'].values]

In [ ]:
results = Parallel(n_jobs=num_cores)(delayed(generateskipgrams)(kmers) for kmers in kmersindex[20000:])
word_target = []
word_context = []
labels = []
for sample in results:
    if type(sample) == tuple:
        word_target += sample[0]
        word_context += sample[1]
        labels += sample[2]
del results

In [ ]:
#Sample 50S ribosome-binding GTPase and equal amount of negative cases
def SampleBinaryClassification(table, function,ProtVecs):
    pos = table.loc[table['FamilyDescription'] == function]
    neg = table.loc[table['FamilyDescription'] != function]
    pos['binarylabel'] = np.ones(len(pos), dtype=bool)
    neg = neg.sample(frac=len(pos)/len(neg))
    neg['binarylabel'] = np.zeros(len(neg), dtype=bool)
    pos = pos.append(neg)
    pos = pos.sample(frac=1)
    #print("Generating ProtVecs")
    #ProtVecs = Parallel(n_jobs=num_cores)(delayed(protvec)(len(threemers), threemersidx, seq, embeddingMat) for seq in pos['Sequence'])
    #pos['ProtVecs'] = ProtVecs
    features = formatprotvecs(ProtVecs)
    BinaryClassification(features,pfambinary['binarylabel'].values)
    return pos


In [ ]:
#ProtVecs = Parallel(n_jobs=num_cores)(delayed(protvec)(threemersidx, seq, embeddingMat) for seq in pfambinary['Sequence'])

In [ ]:
SampleBinaryClassification(swissprot,'50S ribosome-binding GTPase',famclass.iloc[pfambinary.index].values)

In [ ]:
features = formatprotvecsnormalized(famclass.iloc[pfambinary.index].values)
#labels = LabelBinarizer().fit_transform(pfambinary['binarylabel'].values)
BinaryClassification(features,pfambinary['binarylabel'].values)

In [ ]:
features = formatprotvecsnormalized(famclass.iloc[pfambinary.index].values)
#labels = LabelBinarizer().fit_transform(pfambinary['binarylabel'].values)
BinaryClassification(features,pfambinary['binarylabel'].values)

In [ ]:
labels = pfambinary['binarylabel'].values
def fit_model(X, y, clf):
    cv_sets = ShuffleSplit(X.shape[0], n_iter = 5, test_size = 0.20, random_state = 42)
    params = {'C':np.arange(10,100),
             'gamma':np.arange(1e-2,1e-1)}
    grid = GridSearchCV(clf, params, cv=cv_sets, n_jobs=-1)
    grid = grid.fit(X, y)
    return grid.best_params_, grid.best_score_, grid.best_estimator_

best_params, best_score, optimal_svm=fit_model(features,labels,SVC())

print("The best parameters are %s with a score of %0.2f"
      % (best_params, best_score))
print(optimal_svm)

name=["Optimized SVM"]
print(name)
#scores=cross_val_score(optimal_gb,inputfeatures[featurelist], malignantlabel, cv=5, scoring='neg_log_loss')
#print(-scores)
#print("Cross-validated logloss",-np.mean(scores))
print("---------------------------------------")
clf=optimal_svm
clf.fit(features[train],labels[train])
print(classification_report(labels[test],clf.predict(features[test])))
print(confusion_matrix(labels[test],clf.predict(features[test])))
#roc=roc_curve(Ytest,clf.predict_proba(Xtest[featurelist])[:,1])
#print(clf.feature_importances)
#ROC curve
#plt.plot(roc[0],roc[1], alpha=0.5)
#plt.plot(rocrandom[0],rocrandom[1])

#scores=cross_val_score(GradientBoostingClassifier(),inputfeatures[featurelist], malignantlabel, cv=5, scoring='neg_log_loss')
#print(classification_report(Ytest,model.predict(Xtest[featurelist])))
#print(-scores)
#print("Cross-validated logloss",-np.mean(scores))
#print("---------------------------------------")
#clf=SVC()
#clf.fit(Xtrain[featurelist],Ytrain)
#roc=roc_curve(Ytest,clf.predict_proba(Xtest[featurelist])[:,1])

In [ ]:
#Collect cherry annotated dataset
#Import into R and use bioconductor to translate DNAseqs to AASeqs
#Get protvecs for each AAseq
#Load into classifier to determine prediction rate for each category

In [38]:
cherryseqs = pd.read_csv("cherryaaseqs.csv")

In [63]:
num_cores = multiprocessing.cpu_count()
embeddingweights = model.layers[2].get_weights()[0]
cherryProtVecs = Parallel(n_jobs=num_cores)(delayed(protvec)(threemersidx, seq, embeddingMat) for seq in cherryunq['Protein'])

In [64]:
#cherry.to_csv("CherryLabeledMeta.csv",index=False)
cherryprotvecsdf = pd.DataFrame(formatprotvecs(cherryProtVecs))
#cherryprotvecsdf.to_csv("CherryAllProtVecs20millionEpochs.csv",index=False)
cherryprotvecsdf.to_csv("CherryAllProtVecs.csv",index=False)

In [30]:
embeddingweights = model.layers[2].get_weights()[0]
swissprotvecs = Parallel(n_jobs=num_cores)(delayed(protvec)(threemersidx, seq, embeddingweights) for seq in swissprot['Sequence'])

In [31]:
swissprotvecsdf = pd.DataFrame(formatprotvecs(swissprotvecs))
swissprotvecsdf.to_csv("SwissProtVecs10millionEpochsSwissdat.csv",index=False)

In [39]:
from gensim.test.utils import common_texts, get_tmpfile
from gensim.models import Word2Vec

len(common_texts)
path = get_tmpfile("word2vec.model")
model = Word2Vec(common_texts, size=100, window=5, min_count=1, workers=4)
model.save("word2vec.model")